# Prep

Setting up some prior functionality

In [1]:
import shutil

original="../input/motivepredata/MotiveChallenge"
target="/kaggle/working/MotiveChallenge/"
shutil.copytree(original,target)


'/kaggle/working/MotiveChallenge/'

In [2]:
!pip install pycocotools
!pip install torch==1.8.0 torchvision==0.9.0 -qq

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 106.6/106.6 KB 513.1 kB/s eta 0:00:00
  Installing build dependencies ... - \ | / - \ | / - \ | done
  Getting requirements to build wheel ... - \ | / done
  Preparing metadata (pyproject.toml) ... - \ | / done
  Created wheel for pycocotools: filename=pycocotools-2.0.4-cp37-cp37m-linux_x86_64.whl size=370010 sha256=c6805bef48b22398647bb98a90eb50460e6361e98b75bb8a4251e78345563e33
  Stored in directory: /root/.cache/pip/wheels/a3/5f/fa/f011e578cc76e1fc5be8dce30b3eb9fd00f337e744b3bba59b
Successfully built pycocotools


In [3]:
cd '/kaggle/working/MotiveChallenge/detr-master/'

/kaggle/working/MotiveChallenge/detr-master


In [4]:
import torch, torchvision
print(torch.__version__, torch.cuda.is_available())

1.8.0 True


# Load a model

First we have to decide if our model should be pretrained. 

This greatly depends on the size of a dataset. Smaller datasets rely more on finetuning. 

In [5]:
pretrained = True

if pretrained:
    # Get pretrained weights
    checkpoint = torch.hub.load_state_dict_from_url(
                url='https://dl.fbaipublicfiles.com/detr/detr-r50-e632da11.pth',
                map_location='cpu',
                check_hash=True)

    # Remove class weights
    del checkpoint["model"]["class_embed.weight"]
    del checkpoint["model"]["class_embed.bias"]
    del checkpoint["model"]["query_embed.weight"]

    # SaveOGH
    torch.save(checkpoint,
               'detr-r50_no-class-head.pth')

Downloading: "https://dl.fbaipublicfiles.com/detr/detr-r50-e632da11.pth" to /root/.cache/torch/hub/checkpoints/detr-r50-e632da11.pth


  0%|          | 0.00/159M [00:00<?, ?B/s]

# Dataset

Our dataset should be loadable as a COCO format

This allows us to use the pycocotools to load the data dict for the main python script

In [6]:
dataset_file = "coco" # alternatively, implement your own coco-type dataset loader in datasets and add this "key" to datasets/__init__.py

dataDir="/kaggle/working/MotiveChallenge/data" # should lead to a directory with a train2017 and val2017 folder as well as an annotations folder
num_classes = 5 # this int should be the actual number of classes + 1 (for no class)
resume='/kaggle/working/MotiveChallenge/detr-master/detr-r50_no-class-head.pth'
outDir = 'outputs'
#resume = "detr-r50_no-class-head.pth" if pretrained else ""

# Training

We use the main.py script to run our training

In [7]:
pwd

'/kaggle/working/MotiveChallenge/detr-master'

In [8]:
!python main.py \
  --dataset_file $dataset_file \
  --coco_path $dataDir \
  --output_dir $outDir \
  --resume $resume \
  --num_classes $num_classes \
  --lr 1e-5 \
  --lr_backbone 1e-6 \
  --epochs 10\
  --batch_size 8\
  --num_queries 100

Not using distributed mode
fatal: not a git repository (or any parent up to mount point /kaggle)
Stopping at filesystem boundary (GIT_DISCOVERY_ACROSS_FILESYSTEM not set).
git:
  sha: N/A, status: clean, branch: N/A

Namespace(aux_loss=True, backbone='resnet50', batch_size=8, bbox_loss_coef=5, clip_max_norm=0.1, coco_panoptic_path=None, coco_path='/kaggle/working/MotiveChallenge/data', dataset_file='coco', dec_layers=6, device='cuda', dice_loss_coef=1, dilation=False, dim_feedforward=2048, dist_url='env://', distributed=False, dropout=0.1, enc_layers=6, eos_coef=0.1, epochs=10, eval=False, frozen_weights=None, giou_loss_coef=2, hidden_dim=256, lr=1e-05, lr_backbone=1e-06, lr_drop=200, mask_loss_coef=1, masks=False, nheads=8, num_classes=5, num_queries=100, num_workers=2, output_dir='outputs', position_embedding='sine', pre_norm=False, remove_difficult=False, resume='/kaggle/working/MotiveChallenge/detr-master/detr-r50_no-class-head.pth', seed=42, set_cost_bbox=5, set_cost_class=1, set_

# Results

Quick and easy overview of the training results